In [1]:
import networkx as nx
from twitter_api import API_HANDLER as TW
from localsettings import DATA_PATH # modificar para reporte actual
import json

from os.path import join

Switching to API Credentials #14


In [2]:
cuentas = [
    'PabloCarroOk',
    'MartinLlaryora',
]

In [3]:
g = nx.DiGraph()

In [5]:
for name in cuentas:
    u = TW.conn_.get_user(name)
    fids = TW.traer_seguidores(screen_name=name)
    g.add_edges_from([(fid, u.id) for fid in fids])

fetched 2418 followers so far.
fetched 5000 followers so far.
fetched 10000 followers so far.
fetched 15000 followers so far.
fetched 20000 followers so far.
fetched 25000 followers so far.
fetched 30000 followers so far.
fetched 35000 followers so far.
Switching to API Credentials #15
fetched 40000 followers so far.
fetched 44774 followers so far.


In [ ]:
# saving to file

In [6]:
graphpath = join(DATA_PATH, 'red_carro_llaryora.graphml')
nx.write_graphml(g, graphpath)

In [7]:
g.number_of_edges()

47192

In [8]:
g.number_of_nodes()

46696

# Seguidores comunes

In [9]:
cand_uids = [TW.conn_.get_user(name).id for name in cuentas]

In [11]:
comunes = set(g.predecessors(cand_uids[0])).intersection(g.predecessors(cand_uids[1]))

In [12]:
len(comunes)

498

# Relaciones entre seguidores comunes

In [14]:
gcom = g.subgraph(comunes)

In [32]:
failed = []

In [33]:
from tweepy import TweepError

In [34]:
for uid in comunes:
    try:
        fids = set(TW.traer_seguidos(user_id=int(uid))).intersection(comunes)
        gcom.add_edges_from([(uid, fid) for fid in fids])
        print(uid)
    except TweepError, e:
        print(e)
        failed.append(uid)
        continue

884543598221565958
753024776
813734493676826624
151141993
773275048207585280
846248742122610688
870802075797553152
194646577
195190365
369781015
843522207322165248
159871650
190033652
840295404373712896
Switching to API Credentials #1
846242384543387648
737113000520372224
3245827084
1143162512
1692299712
Not authorized.
236571368
Failed to send request: HTTPSConnectionPool(host='api.twitter.com', port=443): Max retries exceeded with url: /1.1/friends/ids.json?cursor=-1&count=5000&user_id=3025622465 (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x7f01a45eb710>: Failed to establish a new connection: [Errno -2] Name or service not known',))
865216724404248576
194153632
429182272
1923164934
3428831505
1387613102
Failed to send request: HTTPSConnectionPool(host='api.twitter.com', port=443): Max retries exceeded with url: /1.1/friends/ids.json?cursor=-1&count=5000&user_id=315294992 (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnecti

In [36]:
graphpath = join(DATA_PATH, 'red_carro_llaryora_comunes.graphml')
nx.write_graphml(gcom, graphpath)

# Traemos data de usuarios

In [38]:
users = []
chunk_size = 100
for i in range(0, len(gcom.nodes()), chunk_size):
    users += TW.conn().lookup_users(gcom.nodes()[i:i+chunk_size])

Switching to API Credentials #17


In [39]:
users

[User(follow_request_sent=None, has_extended_profile=False, profile_use_background_image=True, _json={u'follow_request_sent': None, u'has_extended_profile': False, u'profile_use_background_image': True, u'default_profile_image': False, u'id': 767736648905916416, u'profile_background_image_url_https': None, u'verified': False, u'translator_type': u'none', u'profile_text_color': u'333333', u'profile_image_url_https': u'https://pbs.twimg.com/profile_images/768973183923941376/_tDn6vt8_normal.jpg', u'profile_sidebar_fill_color': u'DDEEF6', u'entities': {u'description': {u'urls': []}}, u'followers_count': 13, u'profile_sidebar_border_color': u'C0DEED', u'id_str': u'767736648905916416', u'profile_background_color': u'F5F8FA', u'listed_count': 0, u'status': {u'contributors': None, u'truncated': False, u'text': u'@DelaSotaOk @NazarioOk y uds nos endeudaron por siglos... Mejor rezarle a Sta Teresa no? Jose Manuel de los comandos civiles De La Sota.', u'is_quote_status': False, u'in_reply_to_stat

In [40]:
import codecs

In [41]:
usersgraphdatapath = join(DATA_PATH, 'comunescarrollaryora.csv') 
with codecs.open(usersgraphdatapath, 'w', encoding='utf-8') as f:
    f.write('id,Label,creada,followers,followed\n')
    for u in users:
        uname = u.screen_name
        f.write('%d,%s,%s,%d,%d\n' % (u.id, uname, str(u.created_at), u.followers_count, u.friends_count, ))